# Traning Data for GEN7 Finetuning 
We train GEN6 with 400% synthetic data thus we can just use the data/sd/gen6/gen6_sd.txt which is about four times the size as the human data file with which we trained GEN0 data/hd/combined0/train_combined0.txt.

In [1]:
import random
import os

def read_data(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        data = file.read().strip().split('\n\n')
    return data

def write_data(data, file_path):
    with open(file_path, 'w', encoding='utf-8') as file:
        file.write('\n\n'.join(data))

def get_file_size(filename):
    """Returns the size of the file in bytes."""
    return os.path.getsize(filename)


In [3]:
print("Original GEN0 HD Size: ", get_file_size("data/hd/combined0/train_combined0.txt"))
print("Training Dataset for GEN6 Size: ", get_file_size("data/sd/opt125m/gen6/gen6_sd_rp1.0.txt"))

Original GEN0 HD Size:  283880989
Training Dataset for GEN6 Size:  567802911


# Finetuning

Finetune the model GEN7 for 5 epochs with 400% synthetic data from GEN6.  
The global_step parameter in "models/distilgpt2-finetuned_gen6_0/trainer_state.json" and "models/distilgpt2-finetuned_gen6_0/checkpoint-19300/trainer_state.json" is originally "global_step": 19300, but in order to force run_clm.py to  
train the model from the last checkpoint with the new dataset we set this parameter to 0 to force it to learn from the entirety of the new dataset. 

### distilgpt2

In [4]:
!deepspeed run_clm.py \
    --model_name_or_path distilgpt2 \
    --train_file data/sd/gen6/gen6_sd.txt \
    --validation_file data/hd/initial_combined/valid_combined.txt \
    --do_train \
    --do_eval \
    --output_dir ./models/distilgpt2-finetuned_gen7_0 \
    --num_train_epochs 5 \
    --save_strategy epoch \
    --learning_rate 5e-5 \
    --per_device_train_batch_size 4 \
    --gradient_accumulation_steps 4 \
    --deepspeed ds_config.json \
    --resume_from_checkpoint ./models/distilgpt2-finetuned_gen6_0/checkpoint-19300


[2024-05-05 17:07:07,243] [INFO] [real_accelerator.py:191:get_accelerator] Setting ds_accelerator to cuda (auto detect)
[2024-05-05 17:07:07,933] [WARNING] [runner.py:202:fetch_hostfile] Unable to find hostfile, will proceed with training with local resources only.
[2024-05-05 17:07:07,944] [INFO] [runner.py:568:main] cmd = /home/vasi/Documents/BA_Thesis_Experiment/.venv/bin/python -u -m deepspeed.launcher.launch --world_info=eyJsb2NhbGhvc3QiOiBbMCwgMV19 --master_addr=127.0.0.1 --master_port=29500 --enable_each_rank_log=None run_clm.py --model_name_or_path distilgpt2 --train_file data/sd/gen6/gen6_sd.txt --validation_file data/hd/initial_combined/valid_combined.txt --do_train --do_eval --output_dir ./models/distilgpt2-finetunes_gen7_0 --num_train_epochs 5 --save_strategy epoch --learning_rate 5e-5 --per_device_train_batch_size 4 --gradient_accumulation_steps 4 --deepspeed ds_config.json --resume_from_checkpoint ./models/distilgpt2-finetuned_gen6_0/checkpoint-19300
[2024-05-05 17:07:09,

In [1]:
!PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True

In [2]:
!deepspeed run_clm.py \
    --model_name_or_path "facebook/opt-125m" \
    --train_file data/sd/opt125m/gen6/gen6_sd_rp1.1.txt \
    --validation_file data/hd/initial_combined/valid_combined.txt \
    --do_train \
    --do_eval \
    --output_dir ./models/OPT/opt-finetuned_gen7_0_1.1 \
    --num_train_epochs 5 \
    --save_strategy epoch \
    --per_device_train_batch_size 2 \
    --gradient_accumulation_steps 16 \
    --deepspeed ds_config_AdamW.json \
    --learning_rate 5e-5 \
    --weight_decay 0.01 \
    --warmup_steps 300 \
    --resume_from_checkpoint ./models/OPT/opt-finetuned_gen6_0_1.1/checkpoint-9020

[2024-06-26 08:16:11,134] [INFO] [real_accelerator.py:191:get_accelerator] Setting ds_accelerator to cuda (auto detect)
[2024-06-26 08:16:11,849] [WARNING] [runner.py:202:fetch_hostfile] Unable to find hostfile, will proceed with training with local resources only.
[2024-06-26 08:16:11,861] [INFO] [runner.py:568:main] cmd = /home/vasi/Documents/BA_Thesis_Experiment/.venv/bin/python -u -m deepspeed.launcher.launch --world_info=eyJsb2NhbGhvc3QiOiBbMCwgMV19 --master_addr=127.0.0.1 --master_port=29500 --enable_each_rank_log=None run_clm.py --model_name_or_path facebook/opt-125m --train_file data/sd/opt125m/gen6/gen6_sd_rp1.1.txt --validation_file data/hd/initial_combined/valid_combined.txt --do_train --do_eval --output_dir ./models/OPT/opt-finetuned_gen7_0_1.1 --num_train_epochs 5 --save_strategy epoch --per_device_train_batch_size 2 --gradient_accumulation_steps 16 --deepspeed ds_config_AdamW.json --learning_rate 5e-5 --weight_decay 0.01 --warmup_steps 300 --resume_from_checkpoint ./model

### **Inference**

For inference, we intend for the model to generate 100 stories using the first 100 prompts from the original RD dataset containing just human prompts for testing('data/hd/prepro/test.wp_source').

In [1]:
with open("data/hd/prepro/test.wp_source") as pfile:
    prompts = pfile.readlines()

# clear starting characters and limit set to first 100 prompts
prompts = [prompt[6:] for prompt in prompts][:100] 
# check for right length
print(len(prompts))

100


In [7]:
from transformers import GPT2LMHeadModel, GPT2Tokenizer


model_name = "./models/distilgpt2-finetuned_gen7_0/checkpoint-38615"
tokenizer = GPT2Tokenizer.from_pretrained(model_name)
model = GPT2LMHeadModel.from_pretrained(model_name)

for prompt in prompts:
    inputs = tokenizer.encode(prompt, add_special_tokens=False, return_tensors="pt")

    # Generate text
    output_sequences = model.generate(
        input_ids=inputs,
        attention_mask=None,
        max_length=500,  # determines the maximum length of the generated text
        temperature=0.7,  # controls randomness: lower values make text less random
        top_k=50,  # the K most likely next words are considered for each step
        top_p=0.9,  # only the most probable tokens with probabilities that add up to top_p are considered for each step
        repetition_penalty=1.2,  # penalty applied to repeated words
        do_sample=True,  # set to True to return diverse samples
        num_return_sequences=1,  # number of independently computed samples to generate
        pad_token_id=tokenizer.eos_token_id,
    )

    # Decode the output sequences to get the generated text
    generated_text = tokenizer.decode(output_sequences[0], skip_special_tokens=True)
    # Leave out the prompt, just write the story to the file
    generated_story = generated_text.split("\n")[1]

    with open("./outputs/gen7/stories7.txt", "a") as f:
        f.write(generated_story + "\n\n")

### OPT 125m

In [5]:
from transformers import OPTForCausalLM, AutoTokenizer
import torch
import re
from tools.sd_generation import inference_stories_batch
from tools.string_tools import selective_normalize_spaced_text

model_name = "models/OPT/opt-finetuned_gen7_0_1.1/checkpoint-9125"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = OPTForCausalLM.from_pretrained(model_name)

min_length = 300
token_length = 0
rp = 1.1

# Define the device based on CUDA availability
device = "cuda" if torch.cuda.is_available() else "cpu"

if tokenizer.pad_token is None:
    tokenizer.pad_token = tokenizer.eos_token

if torch.cuda.is_available():
    model = torch.nn.DataParallel(model)
    model.cuda()
else:
    model.to("cpu")

batch_size = 10



with open(f"./outputs/opt125m/gen7_1.1/stories_opt_gen7_rp{str(rp)}.txt", 'a', encoding='utf-8') as file:
    for i in range(0, len(prompts), batch_size):
        batch_prompts = prompts[i:i + batch_size]
        print(i + batch_size)
        generated_stories = inference_stories_batch(model, tokenizer, device, batch_prompts, min_length, rp)
        
        for generated_story in generated_stories:
            generated_story = re.sub(r'[^a-zA-Z\s.]', '', generated_story)
            generated_story = re.sub(r'^\s+', '', generated_story)
            # write to file
            file.write(generated_story + "\n\n")
                

Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


10
Intermittend length: 1  457
Intermittend length: 2  457
Intermittend length: 3  457
Intermittend length: 4  420
Intermittend length: 5  388
Intermittend length: 6  452
Intermittend length: 7  446
Intermittend length: 8  457
Intermittend length: 9  452
Intermittend length: 10  451
Final length:  451
20
Intermittend length: 1  456
Intermittend length: 2  455
Intermittend length: 3  423
Intermittend length: 4  392
Intermittend length: 5  438
Intermittend length: 6  456
Intermittend length: 7  378
Intermittend length: 8  456
Intermittend length: 9  456
Intermittend length: 10  456
Final length:  456
30
Intermittend length: 1  428
Intermittend length: 2  425
Intermittend length: 3  426
Intermittend length: 4  428
Intermittend length: 5  428
Intermittend length: 6  428
Intermittend length: 7  428
Intermittend length: 8  404
Intermittend length: 9  428
Intermittend length: 10  411
Final length:  411
40
Intermittend length: 1  456
Intermittend length: 2  456
Intermittend length: 3  384
Inte

### **Linguistic Diversity Evaluation**
To assess the linguistic quality of the 100 stories generated by the model, we will evaluate them against a comprehensive set of linguistic metrics. The results will be recorded in a CSV file located at ./outputs/[Current_Gen_Name]. The last line of the file will display the average score for each metric, reflecting the model's mean performance across the selected linguistic dimensions.

In [9]:
from metrics.LexicalDiversity.lexical_diversity import *
from metrics.SemanticDiversity.semantic_diversity import *
from metrics.SyntacticDiversity.syntactic_diversity import *
from nltk.tokenize import sent_tokenize
import pandas as pd
import spacy

rp = 1.1

# Define the column names
columns = ["Distinct-2", "Distinct-3", "Self-BLEU", "OV-TTR", "MS-TTR", "S-DIV-AV", "S-DIV-C", "SYN-DIV"]

# Create an empty DataFrame with these columns
df_eval = pd.DataFrame(columns=columns)

# Load a spaCy model for dependency parsing
nlp = spacy.load("en_core_web_sm")

with open(f"./outputs/opt125m/gen7_1.1/stories_opt_gen7_rp{str(rp)}.txt", 'r') as f:
    stories = f.read().split("\n\n")

for story in stories:
    print(stories.index(story))
    if story != '':

        # Tokenize the text into sentences
        sentences = sent_tokenize(story)
        graphs = construct_dependency_graphs(sentences)

        #A new row of data
        new_data = {
            "Distinct-2": calculate_distinct_n(story, 2),
            "Distinct-3": calculate_distinct_n(story, 3),
            "Self-BLEU": 1-calculate_self_bleu(sentences),
            "OV-TTR": calculate_ttr(story, truncate_length=300),
            "MS-TTR": calculate_mean_segmental_ttr(story, segment_size=50),
            "S-DIV-AV": calculate_semantic_diversity(sentences, 'average'),
            "S-DIV-C": calculate_semantic_diversity(sentences, 'centroid'),
            "SYN-DIV": calculate_syntactic_diversity(graphs)
        }

        # Convert new_data dictionary to a DataFrame
        new_row_df = pd.DataFrame([new_data])
        #print(new_row_df)
        # Concatenate the new row DataFrame to the original DataFrame
        df_eval = pd.concat([df_eval, new_row_df], ignore_index=True)
            

# Calculate the mean for each column and append as a new row
averages = df_eval.mean().to_dict()
averages = {key: [value] for key, value in averages.items()}  # Convert each mean value into a list
average_df = pd.DataFrame(averages)  # Create a DataFrame for the averages
average_df.index = ['Average']  # Label the index as 'Average'

# Append the average row to the original DataFrame
df = pd.concat([df_eval, average_df])

# Specify the file path and name
file_path = f'./outputs/opt125m/gen7_1.1/lg_eval_table_gen7_rp{str(rp)}.csv'

# Write the DataFrame to a CSV file
df.to_csv(file_path, index=False)  # Set index=False to not include row indices in the file

print(f"Data has been written to {file_path}")
# Print the last row (average values)
print("Average values for each metric:")
print(df.iloc[-1])

0


/home/vasi/Documents/BA_Thesis_Experiment/.venv/lib/python3.10/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/home/vasi/Documents/BA_Thesis_Experiment/.venv/lib/python3.10/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/home/vasi/Documents/BA_Thesis_Experiment/.venv/lib/python3.10/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram over

1
2
3
4
5
6
7
8
9
10
11
12
13


/home/vasi/Documents/BA_Thesis_Experiment/.venv/lib/python3.10/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/home/vasi/Documents/BA_Thesis_Experiment/.venv/lib/python3.10/site-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
Data has been written to ./outputs/opt125m/gen7_1.1/lg_eval_table_gen7_rp1.1.csv
Average values for each metric:
Distinct-2    0.694580
Distinct-3    0.709562
Self-BLEU     0.899720
OV-TTR        0.556145
MS-TTR        0.698742
S-DIV-AV      0.802896
S-DIV-C       0.459464
SYN-DIV       0.684074
Name: Average, dtype: float64


### **Literary Evaluation**
To assess the literary quality of the 100 stories generated by the model, we will evaluate them against a comprehensive set of metrics designed to mimic metrics and methods used by humans to evaluate literary outputs. The results again will be recorded in a CSV file located at ./outputs/[Current_Gen_Name]. This time each metric function returns the average of all 100 stories per metric so our CSV will only have one row.

#### **Preparation** : Keyword Categories
To facilitate flexibility calculation, a dictionary is crafted that categorizes words from the RD test prompt file into thematic clusters. We intentionally employ the prompt file for this purpose, believing that this approach establishes a nuanced connection between the flexibility metric and the literary themes intended by the prompts. This connection enhances the metric's relevance, aligning it more closely with how a human would assess creative text.

Steps Involved:
- Preprocessing: The text undergoes preprocessing, which entails cleaning it by removing punctuation and numerical characters while converting it to lowercase for consistency.
- Document-Term Matrix Construction: The preprocessed text is transformed into a document-term matrix through the use of the CountVectorizer.
- Latent Dirichlet Allocation (LDA) Topic Modeling: The LDA model is used to identify clusters of words (topics) that frequently occur together in the text.
- Topic Extraction: Each topic is characterized by the top 10 words associated with it, which are selected to represent the topic.

In [10]:
import re
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import LatentDirichletAllocation

# Load and preprocess the text
with open("data/hd/prepro/test.wp_source") as pfile:
    prompts = pfile.readlines()

prompts = [prompt[6:] for prompt in prompts] # Remove starting characters
prompts = [re.sub(r'[^a-zA-Z\s]', '', prompt.lower()) for prompt in prompts] # Preprocess each prompt separately

# Convert the prompts into a document-term matrix
vectorizer = CountVectorizer(stop_words='english')
X = vectorizer.fit_transform(prompts)

# Fit LDA to find topics
n_topics = 100  # Adjust the number of topics based on experimentation
lda = LatentDirichletAllocation(n_components=n_topics, random_state=42)
lda.fit(X)

# Extract the words associated with each topic
feature_names = vectorizer.get_feature_names_out()
category_keywords = {}

for topic_idx, topic in enumerate(lda.components_):
    keywords = [feature_names[i] for i in topic.argsort()[:-11:-1]]
    category_keywords[f'topic_{topic_idx}'] = keywords

print(category_keywords)

{'topic_0': ['family', 'bathroom', 'knowing', 'turn', 'reason', 'lyrics', 'short', 'judge', 'story', 'songs'], 'topic_1': ['people', 'day', 'locked', 'member', 'marriage', 'just', 'life', 'bedroom', 'trying', 'living'], 'topic_2': ['god', 'dead', 'heaven', 'sins', 'does', 've', 'dying', 'like', 'life', 'alternate'], 'topic_3': ['door', 'lost', 'time', 'years', 'ancient', 'people', 'knock', 'buried', 'nt', 'ability'], 'topic_4': ['nt', 'day', 'ago', 'does', 'longer', 'live', 'world', 'away', 'people', 'left'], 'topic_5': ['life', 'time', 'suicide', 'people', 'commit', 'nt', 'lies', 'decides', 'man', 'end'], 'topic_6': ['changes', 'year', 'life', 'security', 'time', 'world', 'person', 'assassin', 'old', 'important'], 'topic_7': ['conversation', 'human', 'moon', 'water', 'man', 'wants', 'night', 'place', 'soft', 'girl'], 'topic_8': ['open', 'just', 'hair', 'black', 'stuck', 'hours', 'little', 'door', 'invented', 'nt'], 'topic_9': ['making', 'just', 'place', 'law', 've', 'hate', 'won', 'lo

#### **Preparation** : Frequency Reference Corpus
We create a frequency reference corpus from the RD test source (containing human stories) calculating the frequency of each word. The frequencies will then be normalized to represent the proportion of each word's occurrence compared to the entire corpus.
Steps involved:   
- Reading the File: The text file is read and processed as a single string.
- Preprocessing and Tokenization: Non-alphabetic characters are removed, and the text is converted to lowercase. The word_tokenize function is used to split the text into individual words.
- Counting Word Frequencies: A Counter is used to count the occurrence of each word.
- Calculating Normalized Frequencies: The word counts are normalized by dividing each word's count by the total number of words to obtain the frequency of each word as a proportion of the entire text.

This way, the reference_corpus_freq dictionary will contain the normalized frequencies of words from RD test data, which can then be used to assess originality using the calculate_originality function.
  
The threshold in the originality function determines how frequently a word appears in the reference corpus to be considered unoriginal. Words that occur less frequently than this threshold are classified as "original" and contribute to the originality score.

In [11]:
import re
from collections import Counter
from nltk import word_tokenize

def create_reference_corpus_freq(file_path):
    # Load the text
    with open(file_path, 'r') as file:
        text = file.read()

    # Basic preprocessing: Remove non-alphabetic characters and make lowercase
    text = re.sub(r'[^a-zA-Z\s]', '', text).lower()
    
    # Tokenize the words
    words = word_tokenize(text)
    
    # Count word frequencies
    word_counts = Counter(words)
    total_words = sum(word_counts.values())
    
    # Calculate normalized frequencies
    reference_corpus_freq = {word: count / total_words for word, count in word_counts.items()}
    
    return reference_corpus_freq

# Example usage
file_path = 'data/hd/prepro/test.wp_target'
reference_corpus_freq = create_reference_corpus_freq(file_path)
print(reference_corpus_freq)

{'the': 0.05027693989010716, 'wet': 5.821736840936351e-05, 'marble': 2.6020403939173758e-05, 'floor': 0.00036993655095340466, 'pressed': 8.410635616702629e-05, 'on': 0.006109801110808416, 'his': 0.008517345556089543, 'cheek': 5.322355351194632e-05, 'like': 0.0029339976684141077, 'a': 0.02170049122054487, 'thousand': 0.00010132187594496449, 'hands': 0.0005695577306685811, 'slapping': 7.3593061646148e-06, 'face': 0.0010373993368476648, 'frozen': 6.018861113202819e-05, 'in': 0.012210271672729553, 'time': 0.0023272491583779197, 'smattering': 2.234075085686636e-06, 'piss': 2.2603583219888315e-05, 'of': 0.01857975115820366, 'rain': 8.804884161235565e-05, 'ignored': 4.507575025826565e-05, 'indignant': 3.2854045377744644e-06, 'mumblings': 3.942485445329357e-07, 'eyes': 0.001508394931383012, 'fluttered': 8.27921943519165e-06, 'pins': 5.7823119864830576e-06, 'and': 0.022974439684112297, 'needs': 7.372447782765898e-05, 'ran': 0.00028293903879313684, 'from': 0.003882559666560351, 'finger': 0.00011

In [15]:
from metrics.diversity_quality_metrics import *
from metrics.flu_flex_ori import *
import pandas as pd

rp = 1.1

# Define the column names
columns = ["Jaccard-Sim-2", "Feature-Based-Sim", "Fluency", "Flexibility", "Originality"]

# Create an empty DataFrame with these columns
df_eval = pd.DataFrame(columns=columns)

with open("data/hd/initial_combined/test_combined.txt", "r") as file:
    real_content = file.read().strip()
    real_stories_prompts = real_content.split("\n\n") # use just the story without the prompt from the real data
    real_stories = [story.split("\n")[1] for story in real_stories_prompts]


with open(f'./outputs/opt125m/gen7_1.1/stories_opt_gen7_rp{str(rp)}.txt', 'r') as file:
    synthed_content = file.read()
    synthed_stories = synthed_content.split('\n\n')  # Each story separated by two newlines


# Example usage: Adding a new row of data to the DataFrame
new_data = {
    "Jaccard-Sim-2": calculate_ms_jaccard(real_stories[:len(synthed_stories)], synthed_stories, n=2, pseudocount=0.5),
    "Feature-Based-Sim": calculate_feature_based_similarity(synthed_stories),
    "Fluency": calculate_fluency(synthed_stories),
    "Flexibility": calculate_flexibility(synthed_stories, category_keywords),
    "Originality": calculate_originality(synthed_stories, reference_corpus_freq, threshold=0.001) #set a low threshold (e.g., 0.001). This will ensure that only very rare words count as original.
}

# Convert new_data dictionary to a DataFrame
new_row_df = pd.DataFrame([new_data])

# Concatenate the new row DataFrame to the original DataFrame
df_eval = pd.concat([df_eval, new_row_df], ignore_index=True)

# Specify the file path and name
file_path = f'./outputs/opt125m/gen7_1.1/ltr_eval_table_gen7_rp{str(rp)}.csv'

# Write the DataFrame to a CSV file
df_eval.to_csv(file_path, index=False)  # Set index=False to not include row indices in the file

print(f"Data has been written to {file_path}")
# Print the last row (average values)
print("Average values for each metric:")
print(df_eval.iloc[-1])


[65, 89, 88, 93, 84, 64, 95, 70, 89, 64, 92, 96, 90, 17, 94, 80, 87, 95, 88, 91, 70, 1, 93, 94, 0, 63, 97, 95, 82, 62, 94, 88, 1, 98, 92, 14, 92, 94, 75, 73, 18, 92, 92, 96, 97, 89, 91, 86, 73, 88, 94, 89, 14, 93, 60, 92, 57, 96, 95, 89, 86, 99, 93, 94, 60, 88, 93, 100, 89, 95, 86, 95, 92, 33, 95, 79, 21, 87, 99, 93, 86, 96, 71, 0, 77, 14, 3, 95, 73, 90, 94, 56, 0, 88, 38, 96, 88, 73, 88, 24, 0]
Data has been written to ./outputs/opt125m/gen7_1.1/ltr_eval_table_gen7_rp1.1.csv
Average values for each metric:
Jaccard-Sim-2        0.421900
Feature-Based-Sim    0.758923
Fluency              1.059208
Flexibility          0.746238
Originality          0.594324
Name: 0, dtype: float64


/tmp/ipykernel_4131/86690690.py:37: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_eval = pd.concat([df_eval, new_row_df], ignore_index=True)


# Generate Synthetic Data
### Step 6
From GEN 4 we change our data paradigm to a fully synthetic loop training each subsequent generation only with a synthetic dataset created by the previous generation. The dataset is still for GEN7 4 times the size of RD0
Contribute to the synthetic dataset by producing stories from the finetuned model.
We use 400% of the original prompt data as our prompt list.

In [4]:
def count_entries(filepath):
    """Counts the number of double-newline-separated entries in a file."""
    with open(filepath, 'r', encoding='utf-8') as file:
        content = file.read().strip()
    return len(content.split('\n\n'))


total_entries = count_entries("./data/hd/combined0/train_combined0.txt")
print("Total entries in GEN0 Dataset with real data: ", total_entries)

sd_entries_count= total_entries
print("100% \of total entries = ", sd_entries_count)

Total entries in GEN0 Dataset with real data:  109040
100% \of total entries =  109040


In [5]:
import random
from transformers import pipeline, set_seed, GPT2LMHeadModel, GPT2Tokenizer
import os

prompts = []
prompt_files = ["train", "test", "valid"]
for name in prompt_files:
    # Path to the file with prompts
    file_path = './data/hd/prepro/'+name+'.wp_source'

    # Read prompts from the file removing the initials [ XX ]
    with open(file_path, 'r', encoding='utf-8') as file:
        prompts += ([line.strip()[7:] for line in file.readlines() if line.strip()])

#print(prompts[0:10])
# Randomly select 100% of the prompts
sample_size = len(prompts)
selected_prompts = random.sample(prompts, 2*int(sd_entries_count))# quadruple the size of sd for this generation

print(len(selected_prompts))
print(selected_prompts[0:10])


218080
['Becoming immortal seemed like a great idea at the time , but now that the world is ending , you are starting to see the drawbacks ...', 'What the numbers really mean', 'Two planets come within range of eachother every 300 years . There is always an ensuing war that lasts the 5 days that the planets are close enough . Each side can only guess at what new technology the other has built since the last time .', "You 've found a cure for cancer by sheer dumb luck while in the lab ! Sadly , you 've accidentally dropped the only sample of the cure into a tray filled with samples of poison which , inconveniently , are the exact same size , shape , and color as the cure . What now ?", ': You have always wanted to tell the village children how much better life was before the apocalypse , but not knowing of any better , they seem perfectly happy .', "Jan 20th , 2017 . *ON FOX NEWS* BREAKING : We 're receiving reports after exiting the White House to end his final day , President Obama ha

In [6]:
import os

def get_file_size(filename):
    """Returns the size of the file in bytes."""
    return os.path.getsize(filename)

gen0_data_filename = './data/hd/combined0/train_combined0.txt'
gen0_data_size = get_file_size(gen0_data_filename)
print(f"The size of '{gen0_data_filename}' is {gen0_data_size} bytes.")
# 100% of gen0_data_size
gen6_sd_target_size = 4*gen0_data_size
print("Target size (400% of GEN0) for SD File for GEN6: ", gen6_sd_target_size)


The size of './data/hd/combined0/train_combined0.txt' is 307558317 bytes.
Target size (400% of GEN0) for SD File for GEN6:  1230233268


A new element for SD7 datset meant for training GEN8 ist that we generate 4 stories for each prompt and also introduce a min_length parameter of 300 tokens to help us reach the target size for the dataset with our limited supply of prompts.

In [7]:
from transformers import GPT2LMHeadModel, GPT2Tokenizer
import torch
import re

model_name = "./models/distilgpt2-finetuned_gen7_0/checkpoint-38615"
tokenizer = GPT2Tokenizer.from_pretrained(model_name, padding_side='left')
model = GPT2LMHeadModel.from_pretrained(model_name)

# Define the device based on CUDA availability
device = "cuda" if torch.cuda.is_available() else "cpu"


if tokenizer.pad_token is None:
    tokenizer.pad_token = tokenizer.eos_token

if torch.cuda.is_available():
    model = torch.nn.DataParallel(model)
    model.cuda()
else:
    model.to("cpu")

batch_size = 64

def generate_text_batch(prompts):
    inputs = tokenizer(prompts, return_tensors="pt", padding=True, truncation=True)
    inputs = {key: value.to(device) for key, value in inputs.items()}  # Move all tensors to the right device
    outputs = model.module.generate(
        **inputs, 
        max_length=500, 
        min_length=300,
        do_sample=True,
        num_return_sequences=1, 
        temperature=0.7,  # More randomness
        repetition_penalty=1.2,  # Increase penalty to reduce repetitions
        top_k=50, 
        top_p=0.9
    )
    return [tokenizer.decode(output, skip_special_tokens=True) for output in outputs]

output_synth_data = './data/sd/gen7/gen7_sd.txt'

try:
    with open(output_synth_data, 'a', encoding='utf-8') as file:
        for i in range(0, len(selected_prompts), batch_size):
            batch_prompts = selected_prompts[i:i + batch_size]
            print(f"Generating text for batch {i//batch_size+1}/{len(selected_prompts)//batch_size}")
            generated_texts = generate_text_batch(batch_prompts)
            
            for prompt, generated_text in zip(batch_prompts, generated_texts):
                prompt_length = len(tokenizer.encode(prompt))
                #print(prompt)
                # Remove the prompt by slicing the tokens to skip the prompt length
                generated_text_tokens = tokenizer.encode(generated_text)[prompt_length:]
                clean_generated_text = tokenizer.decode(generated_text_tokens, skip_special_tokens=True)

                # Remove leading and ending spaces and special characters
                clean_generated_text = re.sub(r'^[\s\WP]+', '', clean_generated_text)
                clean_generated_text = re.sub(r'^[\s\W]+|[\s\W]+$', '', clean_generated_text)


                output_text = f"{prompt}\n{clean_generated_text}\n\n"
                #print(output_text)
                if get_file_size(output_synth_data) < gen6_sd_target_size:
                    file.write(output_text)
                else:
                    print("Target size reached!")
                    break
    print("Finished generating stories.")
except Exception as e:
    print(f"An error occurred: {e}")

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generating text for batch 1/3407


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generating text for batch 2/3407


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


...

Generating text for batch 3406/3407


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generating text for batch 3407/3407


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Generating text for batch 3408/3407
Finished generating stories.


In [7]:
# check total size of generated sd file
print("Target size for GEN4 sd corresponding to 1/1 of original HD data file: ", gen4_sd_target_size)
print("Actual size of GEN2's generated SD file: ", get_file_size(output_synth_data))

Target size for GEN4 sd corresponding to 1/1 of original HD data file:  307558317
Actual size of GEN2's generated SD file:  307566967
